## Loading Dependencies

In [ ]:
!pip install tqdm

In [ ]:
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import seaborn as sns

from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_samples, silhouette_score
from sklearn.pipeline import Pipeline

#from sklearn.datasets import make_classification
from sklearn.datasets import make_blobs

from copy import deepcopy
import plotly.graph_objects as go


## Loading Data

In [ ]:
url_95 = 'https://drive.google.com/file/d/1ukYfAD9sdDNfw9lz4CocN5Gk7C7SCeCy/view?usp=drive_link'
url_95_id = 'https://drive.google.com/uc?id=' + url_95.split('/')[-2]

#url_206 = 'https://drive.google.com/file/d/1sYU22Cw3DG7wycjYQw12mSBf5DThFwob/view?usp=drive_link'
#url_206_id = 'https://drive.google.com/uc?id=' + url_206.split('/')[-2]

url_310 = 'https://drive.google.com/file/d/1sIwCPblFYbBPIPE7sWFwoJDzrnvl_-J3/view?usp=drive_link'
url_310_id = 'https://drive.google.com/uc?id=' + url_310.split('/')[-2]


In [ ]:
df_95 = pd.read_csv(url_95_id)
df_310 = pd.read_csv(url_310_id)

In [46]:
df_206 = pd.read_csv('https://drive.usercontent.google.com/download?id=1sYU22Cw3DG7wycjYQw12mSBf5DThFwob&authuser=0&confirm=t')
df_206

Timestamp  accelX(g)  accelY(g)  accelZ(g)  \
0        09-Apr-2023 09:09:39.979    -0.0725    -0.9272    -0.7220   
1        09-Apr-2023 09:09:39.981    -0.0725    -0.9272    -0.7220   
2        09-Apr-2023 09:09:39.981    -0.0725    -0.9272    -0.7220   
3        09-Apr-2023 09:09:39.985     0.0197    -1.0018    -0.5080   
4        09-Apr-2023 09:09:39.996     0.1890    -1.0938    -0.3944   
...                           ...        ...        ...        ...   
1232542  09-Apr-2023 12:35:52.580     0.2053    -0.4362    -0.7583   
1232543  09-Apr-2023 12:35:52.589     0.1908    -0.4307    -0.8224   
1232544  09-Apr-2023 12:35:52.600     0.2315    -0.4145    -0.8721   
1232545  09-Apr-2023 12:35:52.610     0.2623    -0.3946    -0.9105   
1232546  09-Apr-2023 12:35:52.620     0.2395    -0.4255    -0.9398   

         accelUserX(g)  accelUserY(g)  accelUserZ(g)  gyroX(rad/s)  \
0              -0.0473         0.0011        -0.4685       -0.3570   
1              -0.0249        -0.0319        -0.2194        0.6848   
2              -0.0249        -0.0319        -0.2194        0.6848   
3              -0.0239        -0.0306        -0.2227        0.6996   
4               0.1304        -0.1245        -0.0687        0.6565   
...                ...            ...            ...           ...   
1232542         0.0147        -0.0285         0.1406        0.0272   
1232543        -0.0045        -0.0233         0.0775       -0.1323   
1232544         0.0326        -0.0125         0.0268       -0.2479   
1232545         0.0731         0.0089        -0.0107       -0.2583   
1232546         0.0588        -0.0191        -0.0399       -0.1922   

         gyroY(rad/s)  gyroZ(rad/s)  ...  ActivityType  ActivityConfidence  \
0              0.0006       -0.3407  ...    Stationary                 Low   
1             -0.6088       -0.1956  ...    Stationary                 Low   
2             -0.6088       -0.1956  ...    Stationary                 Low   
3             -0.8581       -0.0679  ...    Stationary                 Low   
4             -1.0381        0.1358  ...    Stationary                 Low   
...               ...           ...  ...           ...                 ...   
1232542        0.2680        0.0528  ...       Unknown                High   
1232543       -0.0718        0.0130  ...       Unknown                High   
1232544       -0.3634       -0.0012  ...       Unknown                High   
1232545       -0.4049        0.0516  ...       Unknown                High   
1232546       -0.2798        0.1132  ...       Unknown                High   

         Pressure(kilopascals)  RelativeAltitude(meters)  magX(µT)  magY(µT)  \
0                      78.7129                    1.9182 -116.1901  -95.9268   
1                      78.7129                    1.9182 -116.1901  -95.9268   
2                      78.7129                    1.9182 -115.9480  -95.7694   
3                      78.7129                    1.9182 -115.9480  -95.7694   
4                      78.7129                    1.9182 -115.9480  -95.7694   
...                        ...                       ...       ...       ...   
1232542                85.8520                 -701.7922  -76.4675 -114.4828   
1232543                85.8520                 -701.7922  -76.4675 -114.4828   
1232544                85.8520                 -701.7922  -76.4675 -114.4828   
1232545                85.8520                 -701.7922  -76.4675 -114.4828   
1232546                85.8520                 -701.7922  -76.8516 -114.1103   

         magZ(µT)  calMagX(µT)  calMagY(µT)  calMagZ(µT)  
0        -76.0076      -4.0338     -40.8268       4.5567  
1        -76.0076      -3.8767     -40.9227       4.6714  
2        -75.5397      -3.8767     -40.9227       4.6714  
3        -75.5397      -3.8767     -40.9227       4.6714  
4        -75.5397      -3.6705     -40.9901       4.8982  
...           ...          ...          ...          ...  
1232542 -120.1253      -0.3278 

In [ ]:
df_95_clean_1 = df_95.drop(columns=['ActivityType', 'ActivityConfidence', 'Pressure(kilopascals)', 'Roll(rads)', 'Pitch(rads)', 'Yaw(rads)'])
df_206_clean_1 = df_206.drop(columns=['ActivityType', 'ActivityConfidence', 'Pressure(kilopascals)', 'Roll(rads)', 'Pitch(rads)', 'Yaw(rads)'])
df_310_clean_1 = df_310.drop(columns=['ActivityType', 'ActivityConfidence', 'Pressure(kilopascals)', 'Roll(rads)', 'Pitch(rads)', 'Yaw(rads)'])

In [ ]:
df_95_clean_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5717 entries, 0 to 5716
Data columns (total 38 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Timestamp                 5717 non-null   object 
 1   accelX(g)                 5717 non-null   float64
 2   accelY(g)                 5717 non-null   float64
 3   accelZ(g)                 5717 non-null   float64
 4   accelUserX(g)             5717 non-null   float64
 5   accelUserY(g)             5717 non-null   float64
 6   accelUserZ(g)             5717 non-null   float64
 7   gyroX(rad/s)              5717 non-null   float64
 8   gyroY(rad/s)              5717 non-null   float64
 9   gyroZ(rad/s)              5717 non-null   float64
 10  m11                       5717 non-null   float64
 11  m12                       5717 non-null   float64
 12  m13                       5717 non-null   float64
 13  m21                       5717 non-null   float64
 14  m22     

In [ ]:
df_310_clean_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18577 entries, 0 to 18576
Data columns (total 38 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Timestamp                 18577 non-null  object 
 1   accelX(g)                 18577 non-null  float64
 2   accelY(g)                 18577 non-null  float64
 3   accelZ(g)                 18577 non-null  float64
 4   accelUserX(g)             18577 non-null  float64
 5   accelUserY(g)             18577 non-null  float64
 6   accelUserZ(g)             18577 non-null  float64
 7   gyroX(rad/s)              18577 non-null  float64
 8   gyroY(rad/s)              18577 non-null  float64
 9   gyroZ(rad/s)              18577 non-null  float64
 10  m11                       18577 non-null  float64
 11  m12                       18577 non-null  float64
 12  m13                       18577 non-null  float64
 13  m21                       18577 non-null  float64
 14  m22   

In [ ]:
df = df_95_clean_1.drop(columns='Timestamp')

In [ ]:
df_95_gen = deepcopy(df_95_clean_1)

#K-Means

## 6 Clusters

In [ ]:
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=6,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='elkan',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.

df_95_gen['Activity'].value_counts()

0    1734
2    1187
1    1050
4     969
3     406
5     371
Name: Activity, dtype: int64

In [47]:
import plotly.express as px

# Assuming df_95_gen contains the data
fig = px.scatter(df_95_gen,
                 x='Timestamp',
                 y='Alt(m)',
                 color='Activity',
                 title='Altitude vs Timestamp with Activity Color',
                 )
fig.update_layout(xaxis_title='Timestamp', yaxis_title='Altitude(m)', coloraxis_colorbar_title='Activity')
fig.show()


# 4 Clusters

In [ ]:
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=4,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='elkan',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data
fig = px.scatter(df_95_gen, x='Timestamp',
                 y='Alt(m)',
                 color='Activity',
                 title='Altitude vs Timestamp with Activity Color',
                 color_discrete_sequence=px.colors.qualitative.T10,
                 )
fig.update_layout(xaxis_title='Timestamp', yaxis_title='Altitude(m)', coloraxis_colorbar_title='Activity')
fig.show()

# Feature Selection


In [ ]:
df_95_clean_1.columns

Index(['Timestamp', 'accelX(g)', 'accelY(g)', 'accelZ(g)', 'accelUserX(g)',
       'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)', 'gyroY(rad/s)',
       'gyroZ(rad/s)', 'm11', 'm12', 'm13', 'm21', 'm22', 'm23', 'm31', 'm32',
       'm33', 'qX', 'qY', 'qZ', 'qW', 'Lat', 'Long', 'Speed(m/s)',
       'TrueHeading', 'Alt(m)', 'HorizontalAccuracy(m)', 'VerticalAccuracy(m)',
       'Course', 'RelativeAltitude(meters)', 'magX(µT)', 'magY(µT)',
       'magZ(µT)', 'calMagX(µT)', 'calMagY(µT)', 'calMagZ(µT)'],
      dtype='object')

In [ ]:
import pandas as pd

# Convert 'Timestamp' column to datetime objects
df_95_gen['Timestamp'] = pd.to_datetime(df_95_gen['Timestamp'])

# Calculate the time difference in seconds
df_95_gen['Time'] = (df_95_gen['Timestamp'] - df_95_gen['Timestamp'].iloc[0]).dt.total_seconds()


In [ ]:
df_fe = df_95_clean_1[[
                       #'accelX(g)', 'accelY(g)', 'accelZ(g)',
                       'accelUserX(g)','accelUserY(g)', 'accelUserZ(g)',
                       'gyroX(rad/s)', 'gyroY(rad/s)','gyroZ(rad/s)',
                       #'m11', 'm12', 'm13', 'm21', 'm22', 'm23', 'm31', 'm32','m33',
                       #'qX', 'qY', 'qZ', 'qW',
                       #'Lat', 'Long',
                       #'Speed(m/s)',
                       #'TrueHeading',
                       #'Alt(m)',
                       #'HorizontalAccuracy(m)', 'VerticalAccuracy(m)',
                       'Course',
                       #'RelativeAltitude(meters)',
                       #'magX(µT)', 'magY(µT)','magZ(µT)',
                       #'calMagX(µT)', 'calMagY(µT)', 'calMagZ(µT)'
                       ]]
df_fe

accelUserX(g)  accelUserY(g)  accelUserZ(g)  gyroX(rad/s)  gyroY(rad/s)  \
0           -0.0108         0.0025        -0.0101        0.0166        0.0051   
1           -0.0094         0.0023         0.0054        0.0042        0.0032   
2           -0.0059         0.0053        -0.0014        0.0020        0.0021   
3           -0.0070         0.0025         0.0136        0.0594        0.0147   
4            0.0065        -0.0080         0.0061       -0.0024        0.0176   
...             ...            ...            ...           ...           ...   
5712         0.0372         0.0828         0.1670       -0.2750        0.2061   
5713         0.0679         0.0978        -0.2162        0.4758       -0.3229   
5714         0.0376         0.0170        -0.5497        0.3940        0.0148   
5715         0.0248        -0.0423         0.0775       -0.1799       -0.2665   
5716        -0.2337         0.0791        -0.0465        0.2664        0.2564   

      gyroZ(rad/s)  Course  
0           0.0318    -1.0  
1          -0.0066    -1.0  
2           0.0225    -1.0  
3           0.0097    -1.0  
4           0.0147    -1.0  
...            ...     ...  
5712        0.1289   330.1  
5713        0.2953   334.6  
5714        0.0588   348.3  
5715       -0.2316   343.8  
5716        0.0798   334.7  

[5717 rows x 7 columns]

In [ ]:
number_of_clusters = 2
algo = 'lloyd'

kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 3
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 4
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 5
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 6
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 7
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 8
algo = 'elkan'

kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


In [ ]:
number_of_clusters = 9
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()


# FE 2

In [ ]:
df_fe2 = df_95_clean_1[[
                       #'accelX(g)', 'accelY(g)', 'accelZ(g)',
                       'accelUserX(g)','accelUserY(g)', 'accelUserZ(g)',
                       'gyroX(rad/s)', 'gyroY(rad/s)','gyroZ(rad/s)',
                       #'m11', 'm12', 'm13', 'm21', 'm22', 'm23', 'm31', 'm32','m33',
                       #'qX', 'qY', 'qZ', 'qW',
                       #'Lat', 'Long',
                       'Speed(m/s)',
                       #'TrueHeading',
                       #'Alt(m)',
                       #'HorizontalAccuracy(m)', 'VerticalAccuracy(m)',
                       'Course',
                       #'RelativeAltitude(meters)',
                       #'magX(µT)', 'magY(µT)','magZ(µT)',
                       #'calMagX(µT)', 'calMagY(µT)', 'calMagZ(µT)'
                       ]]
df_fe2

accelUserX(g)  accelUserY(g)  accelUserZ(g)  gyroX(rad/s)  gyroY(rad/s)  \
0           -0.0108         0.0025        -0.0101        0.0166        0.0051   
1           -0.0094         0.0023         0.0054        0.0042        0.0032   
2           -0.0059         0.0053        -0.0014        0.0020        0.0021   
3           -0.0070         0.0025         0.0136        0.0594        0.0147   
4            0.0065        -0.0080         0.0061       -0.0024        0.0176   
...             ...            ...            ...           ...           ...   
5712         0.0372         0.0828         0.1670       -0.2750        0.2061   
5713         0.0679         0.0978        -0.2162        0.4758       -0.3229   
5714         0.0376         0.0170        -0.5497        0.3940        0.0148   
5715         0.0248        -0.0423         0.0775       -0.1799       -0.2665   
5716        -0.2337         0.0791        -0.0465        0.2664        0.2564   

      gyroZ(rad/s)  Speed(m/s)  Course  
0           0.0318      0.1935    -1.0  
1          -0.0066      0.4469    -1.0  
2           0.0225      0.2260    -1.0  
3           0.0097      0.5294    -1.0  
4           0.0147      0.0000    -1.0  
...            ...         ...     ...  
5712        0.1289      1.1109   330.1  
5713        0.2953      1.0336   334.6  
5714        0.0588      1.1682   348.3  
5715       -0.2316      1.2437   343.8  
5716        0.0798      1.1386   334.7  

[5717 rows x 8 columns]

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['Speed(m/s)', 'Course'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelX(g)', 'accelY(g)', 'accelZ(g)', 'accelUserX(g)', 'accelUserY(g)',
       'accelUserZ(g)', 'gyroX(rad/s)', 'gyroY(rad/s)', 'gyroZ(rad/s)'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelX(g)', 'accelY(g)', 'accelZ(g)', 'accelUserX(g)', 'accelUserY(g)',
       'accelUserZ(g)', 'gyroX(rad/s)', 'gyroY(rad/s)', 'gyroZ(rad/s)',
       'Speed(m/s)'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'

kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelUserX(g)', 'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)',
       'gyroY(rad/s)', 'gyroZ(rad/s)', 'Speed(m/s)', 'Course'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['Speed(m/s)', 'TrueHeading', 'Alt(m)'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['Speed(m/s)', 'TrueHeading', 'Alt(m)'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['Speed(m/s)', 'Course'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['Speed(m/s)', 'TrueHeading'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['Speed(m/s)'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['gyroX(rad/s)', 'gyroY(rad/s)', 'gyroZ(rad/s)', 'Course'], dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelUserX(g)', 'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)',
       'gyroY(rad/s)', 'gyroZ(rad/s)', 'Course'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelX(g)', 'accelY(g)', 'accelZ(g)', 'gyroX(rad/s)', 'gyroY(rad/s)',
       'gyroZ(rad/s)', 'Course'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelUserX(g)', 'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)',
       'gyroY(rad/s)', 'gyroZ(rad/s)', 'Speed(m/s)', 'Course',
       'RelativeAltitude(meters)'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelUserX(g)', 'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)',
       'gyroY(rad/s)', 'gyroZ(rad/s)', 'Speed(m/s)', 'Course',
       'RelativeAltitude(meters)'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelUserX(g)', 'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)',
       'gyroY(rad/s)', 'gyroZ(rad/s)', 'Speed(m/s)', 'Course', 'calMagX(µT)',
       'calMagY(µT)', 'calMagZ(µT)'],
      dtype='object')

In [ ]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe2)  # Compute cluster centers and predict cluster index for each sample.
df_95_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_95_gen['Activity'].value_counts()

# Assuming df_95_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_95_gen['Time'],
    y=df_95_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_95_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe2.columns

Index(['accelUserX(g)', 'accelUserY(g)', 'accelUserZ(g)', 'gyroX(rad/s)',
       'gyroY(rad/s)', 'gyroZ(rad/s)', 'Speed(m/s)', 'Course'],
      dtype='object')

# Testing on 310m File

In [48]:
df_310_gen = deepcopy(df_310_clean_1)


# Convert 'Timestamp' column to datetime objects
df_310_gen['Timestamp'] = pd.to_datetime(df_310_gen['Timestamp'])

# Calculate the time difference in seconds
df_310_gen['Time'] = (df_310_gen['Timestamp'] - df_310_gen['Timestamp'].iloc[0]).dt.total_seconds()


In [53]:
df_fe3 = df_310_clean_1[[
                       'accelX(g)', 'accelY(g)', 'accelZ(g)',
                       'accelUserX(g)','accelUserY(g)', 'accelUserZ(g)',
                       'gyroX(rad/s)', 'gyroY(rad/s)','gyroZ(rad/s)',
                       #'m11', 'm12', 'm13', 'm21', 'm22', 'm23', 'm31', 'm32','m33',
                       #'qX', 'qY', 'qZ', 'qW',
                       #'Lat', 'Long',
                       'Speed(m/s)',
                       #'TrueHeading',
                       #'Alt(m)',
                       #'HorizontalAccuracy(m)', 'VerticalAccuracy(m)',
                       'Course',
                       #'RelativeAltitude(meters)',
                       #'magX(µT)', 'magY(µT)','magZ(µT)',
                       #'calMagX(µT)', 'calMagY(µT)', 'calMagZ(µT)'
                       ]]
df_fe3

accelX(g)  accelY(g)  accelZ(g)  accelUserX(g)  accelUserY(g)  \
0         0.1469    -0.5016    -0.6164        -0.0205         0.0419   
1         0.1552    -0.5138    -0.7686         0.0539        -0.0730   
2         0.1574    -0.6052    -0.8676         0.0057         0.0007   
3         0.4539    -0.5253    -0.7737         0.1758         0.3740   
4         0.3829    -1.1274     0.5387         0.0678        -0.2406   
...          ...        ...        ...            ...            ...   
18572    -0.1306    -0.4372    -1.0096        -0.1329        -0.0651   
18573     0.0719    -0.4624    -0.8884        -0.0267         0.0056   
18574    -0.1669    -0.7570    -0.5373        -0.3806        -0.2018   
18575     0.2455    -0.1281    -1.1840         0.1035        -0.0669   
18576     0.0207    -0.2949    -0.8530        -0.0082         0.0191   

       accelUserZ(g)  gyroX(rad/s)  gyroY(rad/s)  gyroZ(rad/s)  Speed(m/s)  \
0             0.2105       -0.2433       -0.1863        0.1109        3.87   
1             0.1244       -0.2232        0.2461        0.0555        4.70   
2            -0.0876        0.0985       -0.2090        0.0404        4.04   
3            -0.2897        0.2943       -0.1839       -0.0680        7.47   
4             0.3286       -0.4226       -0.4921       -0.7779        8.65   
...              ...           ...           ...           ...         ...   
18572        -0.0815        0.6196        0.5358       -0.1787        0.00   
18573        -0.0102        0.0011       -0.0850       -0.5501        0.00   
18574         0.2665        5.2579       -2.0120        0.9900        0.00   
18575        -0.1960       -0.0707       -0.5946       -0.3314        0.00   
18576         0.0960        0.3310       -0.2671        0.0010        0.00   

       Course  
0       164.5  
1       161.7  
2       161.7  
3       157.5  
4       164.2  
...       ...  
18572    87.3  
18573    87.3  
18574    87.3  
18575    87.3  
18576    87.3  

[18577 rows x 11 columns]

In [54]:
number_of_clusters = 8
algo = 'lloyd'
kmeans_pipeline = Pipeline([
    ("scaler", StandardScaler()),  # Standardize features by removing the mean and scaling to unit variance.
    ("cluster", KMeans(
        n_clusters=number_of_clusters,  # Number of clusters to form.
        init='k-means++',  # Method for initialization: 'k-means++' selects initial cluster centers for k-mean clustering in a smart way to speed up convergence.
        n_init='auto',  # Number of times the k-means algorithm will be run with different centroid seeds. 'auto' chooses min(n_samples, n_clusters) as the number of initializations.
        max_iter=500,  # Maximum number of iterations of the k-means algorithm for a single run.
        tol=1e-4,  # Relative tolerance with regards to inertia to declare convergence.
        algorithm='lloyd',  # K-means algorithm to use. 'lloyd' is the classic algorithm.
        random_state=17,  # Determines random number generation for centroid initialization and random reassignment steps.
        verbose=0  # Verbosity mode. 0 means silent.
    ))
])

# kmeans_pipeline.fit(df)  # Fit the pipeline on the input data.
clusters = kmeans_pipeline.fit_predict(df_fe3)  # Compute cluster centers and predict cluster index for each sample.
df_310_gen['Activity'] = clusters  # Assign cluster labels to the dataframe.
df_310_gen['Activity'].value_counts()

# Assuming df_310_gen contains the data

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_310_gen['Time'],
    y=df_310_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_310_gen['Activity'], colorscale='rainbow', colorbar=dict(title='Activity')),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe3.columns

Index(['accelX(g)', 'accelY(g)', 'accelZ(g)', 'accelUserX(g)', 'accelUserY(g)',
       'accelUserZ(g)', 'gyroX(rad/s)', 'gyroY(rad/s)', 'gyroZ(rad/s)',
       'Speed(m/s)', 'Course'],
      dtype='object')

In [59]:
# Define the function
def on_lift(activity):
    return 1 if activity in [3] else 0

# Apply the function to create the 'on_lift' column
df_310_gen['on_lift'] = df_310_gen['Activity'].apply(lambda x: on_lift(x))


In [76]:

# Create a scatter plot trace
scatter = go.Scatter(
    x=df_310_gen['Time'],
    y=df_310_gen['Alt(m)'],
    mode='markers',
    marker=dict(color=df_310_gen['on_lift'],
                #colorscale='rainbow',
                #colorbar=dict(title='Activity')
                ),
    showlegend=False
)

# Create layout
layout = go.Layout(
    title= str(number_of_clusters) + ' Clusters using ' + algo,
    xaxis=dict(title='Elapsed Time (s)'),
    yaxis=dict(title='Altitude(m)')
)

# Create figure
fig = go.Figure(data=[scatter], layout=layout)

# Show the figure
fig.show()
df_fe3.columns

Index(['accelX(g)', 'accelY(g)', 'accelZ(g)', 'accelUserX(g)', 'accelUserY(g)',
       'accelUserZ(g)', 'gyroX(rad/s)', 'gyroY(rad/s)', 'gyroZ(rad/s)',
       'Speed(m/s)', 'Course'],
      dtype='object')

In [69]:
# Set 'on_lift' column values to 1 where 'Time' column falls within the specified range
timeframes= [[0, 100],
            [430, 720],
             [1705, 1934],
              [2200, 2450],
             [2922, 2190],
             [3510, 3795],
             [5191, 5422],
             [6723, 7047],
             [9398, 9673],
             [10295, 10681],
             [11085, 11441],
             [11686, 11913],
             [12728,13073]
             ]



In [75]:
df_310_gen['on_lift'] = 0
for timeframe in timeframes:
  #print(timeframe[0], timeframe[1])
  df_310_gen.loc[(df_310_gen['Time'] >= timeframe[0]) & (df_310_gen['Time'] <= timeframe[1]), 'on_lift'] = 1


In [77]:
def export_dataframe_to_csv(dataframe, filename):
    dataframe.to_csv(filename, index=False)

# Usage example
export_dataframe_to_csv(df_310_gen, "df_310_labeled_on_lift.csv")
